In [1]:
import matplotlib.pyplot as plt
%matplotlib inline
import time
from csv import reader
import pandas as pd
from collections import defaultdict
from itertools import chain, combinations

In [59]:
def dataFromFile(fname, splitter, front_lim = 0, end_lim = 0):
    """Function which reads from the file and yields a generator"""
    itemSets = []
    #itemSet = set()
    # Open text file
    with open(fname, "r") as file_iter:
        for line in file_iter:
            # Remove trailing commas, spaces, and all other required characters.
            line = line.strip()[front_lim:(-end_lim)]#.rstrip(end_strip).strip() removed it as it removes 
            #all eligible characters passed to end_strip argument.
            record = set([int(ele) for ele in line.split(splitter)])
            #for item in record:
            #    itemSet.add(frozenset([item]))
            itemSets.append(record)
    return itemSets

In [53]:
import csv, itertools


def load_data(filename):
    """
    Loads transactions from given file
    :param filename:
    :return:
    """
    reader = csv.reader(open(filename, 'r'), delimiter=',')
    trans = [[int(ele) for ele in row[1:] if ele.isnumeric()] for row in reader]
    return trans


def find_frequent_one(data_set, support):
    """
    Find frequent one itemsets within data set
    :param data_set:
    :param support: Provided support value
    :return:
    """
    candidate_one = {}
    total = len(data_set)
    for row in data_set:
        for val in row:
            if val in candidate_one:
                candidate_one[val] += 1
            else:
                candidate_one[val] = 1

    frequent_1 = []
    for key, cnt in candidate_one.items():
        # check if given item has sufficient count.
        if cnt >= (support * total / 100):
            frequent_1.append(([key], cnt))
    return frequent_1


class HNode:
    """
    Class which represents node in a hash tree.
    """

    def __init__(self):
        self.children = {}
        self.isLeaf = True
        self.bucket = {}


class HTree:
    """
    Wrapper class for HTree instance
    """

    def __init__(self, max_leaf_cnt, max_child_cnt):
        self.root = HNode()
        self.max_leaf_cnt = max_leaf_cnt
        self.max_child_cnt = max_child_cnt
        self.frequent_itemsets = []

    def recur_insert(self, node, itemset, index, cnt):
        # TO-DO
        """
        Recursively adds nodes inside the tree and if required splits leaf node and
        redistributes itemsets among child converting itself into intermediate node.
        node:
        itemset:
        index:
        
        return:
        """
        if index == len(itemset):
            # last bucket so just insert
            if itemset in node.bucket:
                node.bucket[itemset] += cnt
            else:
                node.bucket[itemset] = cnt
            return

        if node.isLeaf:
            
            if itemset in node.bucket:
                node.bucket[itemset] += cnt
            else:
                node.bucket[itemset] = cnt
            if len(node.bucket) == self.max_leaf_cnt:
                # bucket has reached its maximum capacity and its intermediate node so
                # split and redistribute entries.
                for old_itemset, old_cnt in node.bucket.items():
                    
                    hash_key = self._hash(old_itemset[index])
                    if hash_key not in node.children:
                        node.children[hash_key] = HNode()
                    self.recur_insert(node.children[hash_key], old_itemset, index + 1, old_cnt)
                # there is no point in having this node's bucket
                # so just delete it
                del node.bucket
                node.isLeaf = False
        else:
            hash_key = self._hash(itemset[index])
            if hash_key not in node.children:
                node.children[hash_key] = HNode()
            self.recur_insert(node.children[hash_key], itemset, index + 1, cnt)

    def insert(self, itemset):
        # as list can't be hashed we need to convert this into tuple
        # which can be easily hashed in leaf node buckets
        itemset = tuple(itemset)
        self.recur_insert(self.root, itemset, 0, 0)

    def add_support(self, itemset):
        runner = self.root
        itemset = tuple(itemset)
        index = 0
        while True:
            if runner.isLeaf:
                if itemset in runner.bucket:
                    runner.bucket[itemset] += 1
                break
            hash_key = self._hash(itemset[index])
            if hash_key in runner.children:
                runner = runner.children[hash_key]
            else:
                break
            index += 1

    def dfs(self, node, support_cnt):
        if node.isLeaf:
            for key, value in node.bucket.items():
                if value >= support_cnt:
                    self.frequent_itemsets.append((list(key), value))
                    # print key, value, support_cnt
            return

        for child in node.children.values():
            self.dfs(child, support_cnt)

    def get_frequent_itemsets(self, support_cnt):
        """
        Returns all frequent itemsets which can be considered for next level
        :param support_cnt: Minimum cnt required for itemset to be considered as frequent
        :return:
        """
        self.frequent_itemsets = []
        self.dfs(self.root, support_cnt)
        return self.frequent_itemsets

    def _hash(self, val):
        return val % self.max_child_cnt


def generate_hash_tree(candidate_itemsets, length, max_leaf_cnt = 10, max_child_cnt = 11):
    """
    This function generates hash tree of itemsets with each node having no more than child_max_length
    childs and each leaf node having no more than max_leaf_length.
    :param candidate_itemsets: Itemsets
    :param length: Length if each itemset
    :param max_leaf_length:
    :param child_max_length:
    :return:
    """
    htree = HTree(max_child_cnt, max_leaf_cnt)
    for itemset in candidate_itemsets:
        # add this itemset to hashtree
        htree.insert(itemset)
    return htree


def generate_k_subsets(dataset, length):
    subsets = []
    for itemset in dataset:
        subsets.extend(map(list, itertools.combinations(itemset, length)))
    return subsets


def is_prefix(list_1, list_2):
    for i in range(len(list_1) - 1):
        if list_1[i] != list_2[i]:
            return False
    return True


def apriori_generate_frequent_itemsets(dataset, support):
    """
    Generates frequent itemsets
    :param dataset:
    :param support:
    :return: List of f-itemsets with their respective count in
            form of list of tuples.
    """
    support_cnt = int(support / 100.0 * len(dataset))
    all_frequent_itemsets = find_frequent_one(dataset, support)
    prev_frequent = [x[0] for x in all_frequent_itemsets]
    length = 2
    while len(prev_frequent) > 1:
        new_candidates = []
        for i in range(len(prev_frequent)):
            j = i + 1
            while j < len(prev_frequent) and is_prefix(prev_frequent[i], prev_frequent[j]):
                # this part makes sure that all of the items remain lexicographically sorted.
                new_candidates.append(prev_frequent[i][:-1] +
                                      [prev_frequent[i][-1]] +
                                      [prev_frequent[j][-1]])
                j += 1

        # generate hash tree and find frequent itemsets
        h_tree = generate_hash_tree(new_candidates, length)
        # for each transaction, find all possible subsets of size "length"
        k_subsets = generate_k_subsets(dataset, length)

        # support counting and finding frequent itemsets
        for subset in k_subsets:
            h_tree.add_support(subset)

        # find frequent itemsets
        new_frequent = h_tree.get_frequent_itemsets(support_cnt)
        all_frequent_itemsets.extend(new_frequent)
        prev_frequent = [tup[0] for tup in new_frequent]
        prev_frequent.sort()
        length += 1

    return all_frequent_itemsets

In [54]:
SUPPORT = 0.645
CONFIDENCE = 5

In [55]:
# Import the data...
transactions = dataFromFile("BMSWebView2.txt", " -1 ", front_lim = 0, end_lim = 6)

In [56]:
#transactions = load_data('bakery.csv')
# print find_frequent_one(transactions, 5)
frequent = apriori_generate_frequent_itemsets(transactions, SUPPORT)

In [57]:
len(frequent)

129

In [58]:
frequent

[([55455], 598),
 ([55831], 1291),
 ([55835], 953),
 ([55839], 857),
 ([55863], 635),
 ([56765], 950),
 ([55407], 532),
 ([55331], 775),
 ([55287], 1477),
 ([55323], 3417),
 ([55327], 2150),
 ([55295], 1834),
 ([89845], 544),
 ([89849], 729),
 ([89453], 637),
 ([55283], 2093),
 ([84731], 1226),
 ([55343], 1293),
 ([55859], 1027),
 ([89705], 907),
 ([55319], 2497),
 ([55367], 1296),
 ([82719], 1255),
 ([55559], 1009),
 ([55819], 694),
 ([55315], 2248),
 ([55463], 1046),
 ([55351], 2249),
 ([56761], 2048),
 ([55483], 539),
 ([55487], 869),
 ([55875], 1331),
 ([55883], 745),
 ([56023], 722),
 ([55267], 3766),
 ([56037], 799),
 ([55271], 2284),
 ([56041], 960),
 ([55291], 2003),
 ([55551], 1423),
 ([55871], 1031),
 ([55855], 758),
 ([197025], 840),
 ([55887], 1125),
 ([89721], 940),
 ([55531], 957),
 ([55719], 725),
 ([86911], 665),
 ([55843], 1032),
 ([55867], 757),
 ([56769], 1602),
 ([55555], 786),
 ([55503], 617),
 ([55547], 725),
 ([55539], 582),
 ([203729], 1324),
 ([55275], 1105),
 

In [51]:
def tuple_to_dataframe(frequent):
    """Transforms tuple of itemset and their frequency to dataframe."""
    

In [27]:
transactions = load_data('bakery.csv')

In [11]:
T1 = ['13', '17', '18', '21', '32']
T3 = list(map(int, T1))
T3

[13, 17, 18, 21, 32]

## asaini

In [76]:
# from another library:
"""
Description     : Simple Python implementation of the Apriori Algorithm
Usage:
    $python apriori.py -f DATASET.csv -s minSupport  -c minConfidence
    $python apriori.py -f DATASET.csv -s 0.15 -c 0.6
"""

import sys

from itertools import chain, combinations
from collections import defaultdict
from optparse import OptionParser

def subsets(arr):
    """ Returns non empty subsets of arr"""
    return chain(*[combinations(arr, i + 1) for i, a in enumerate(arr)])


def returnItemsWithMinSupport(itemSet, transactionList, minSupport, freqSet):
    """calculates the support for items in the itemSet and returns a subset
    of the itemSet each of whose elements satisfies the minimum support"""
    _itemSet = set()
    localSet = defaultdict(int)

    for item in itemSet:
        for transaction in transactionList:
            if item.issubset(transaction):
                freqSet[item] += 1
                localSet[item] += 1

    for item, count in localSet.items():
        support = float(count) / len(transactionList)

        if support >= minSupport:
            _itemSet.add(item)

    return _itemSet


def joinSet(itemSet, length):
    """Join a set with itself and returns the n-element itemsets"""
    return set(
        [i.union(j) for i in itemSet for j in itemSet if len(i.union(j)) == length]
    )


def getItemSetTransactionList(data_iterator):
    """This generates Level 1-itemSets"""
    transactionList = []
    itemSet = set()
    for record in data_iterator:
        transaction = frozenset(record)
        transactionList.append(transaction)
        for item in transaction:
            itemSet.add(frozenset([item]))  # Generate 1-itemSets
    return itemSet, transactionList


def runApriori(data_iter, minSupport, minConfidence):
    """
    run the apriori algorithm. data_iter is a record iterator
    Return both:
     - items (tuple, support)
     - rules ((pretuple, posttuple), confidence)
    """
    itemSet, transactionList = getItemSetTransactionList(data_iter)

    freqSet = defaultdict(int)
    largeSet = dict()
    # Global dictionary which stores (key=n-itemSets,value=support)
    # which satisfy minSupport

    assocRules = dict()
    # Dictionary which stores Association Rules

    oneCSet = returnItemsWithMinSupport(itemSet, transactionList, minSupport, freqSet)

    currentLSet = oneCSet
    k = 2
    while currentLSet != set([]):
        largeSet[k - 1] = currentLSet
        currentCSet = joinSet(currentLSet, k)
        currentLSet = returnItemsWithMinSupport(currentCSet, transactionList, minSupport, freqSet)
        k = k + 1

    def getSupport(item):
        """local function which Returns the support of an item"""
        return float(freqSet[item]) / len(transactionList)

    toRetItems = []
    for key, value in largeSet.items():
        toRetItems.extend([(tuple(item), getSupport(item)) for item in value])

    toRetRules = []
    for key, value in list(largeSet.items())[1:]:
        for item in value:
            _subsets = map(frozenset, [x for x in subsets(item)])
            for element in _subsets:
                remain = item.difference(element)
                if len(remain) > 0:
                    confidence = getSupport(item) / getSupport(element)
                    if confidence >= minConfidence:
                        toRetRules.append(((tuple(element), tuple(remain)), confidence))
    return toRetItems, toRetRules


def printResults(items, rules):
    """prints the generated itemsets sorted by support and the confidence rules sorted by confidence"""
    for item, support in sorted(items, key=lambda x: x[1]):
        print("item: %s , %.3f" % (str(item), support))
    print("\n------------------------ RULES:")
    for rule, confidence in sorted(rules, key=lambda x: x[1]):
        pre, post = rule
        print("Rule: %s ==> %s , %.3f" % (str(pre), str(post), confidence))


def to_str_results(items, rules):
    """prints the generated itemsets sorted by support and the confidence rules sorted by confidence"""
    i, r = [], []
    for item, support in sorted(items, key=lambda x: x[1]):
        x = "item: %s , %.3f" % (str(item), support)
        i.append(x)

    for rule, confidence in sorted(rules, key=lambda x: x[1]):
        pre, post = rule
        x = "Rule: %s ==> %s , %.3f" % (str(pre), str(post), confidence)
        r.append(x)

    return i, r


def dataFromFile(fname, splitter, front_lim = 0, end_lim = 0):
    """Function which reads from the file and yields a generator"""
    with open(fname, "r") as file_iter:
        for line in file_iter:
            # Remove trailing commas, spaces, and all other required characters.
            line = line.strip()[front_lim:(-end_lim)]#.rstrip(end_strip).strip() removed it as it removes 
            #all eligible characters passed to end_strip argument.
            record = frozenset(line.split(splitter))
            yield record

In [90]:
# Import the data...
data = list(dataFromFile("BMSWebView2.txt", " -1 ", front_lim = 0, end_lim = 6))

In [93]:
for line in data:
    print(line)

frozenset({'86919', '82475', '84211', '86943', '86927'})
frozenset({'56109', '222699'})
frozenset({'55455'})
frozenset({'81991', '81795'})
frozenset({'56077', '55879', '56373', '55863', '222699', '56225', '55835', '55847', '222607', '55411', '55407', '222511', '55991', '56765', '55435', '222499', '55831', '55895', '55839', '55403'})
frozenset({'55327', '55323', '222331', '222323', '55295', '55287', '55331'})
frozenset({'84947', '84999'})
frozenset({'86003', '82875', '82879'})
frozenset({'85087'})
frozenset({'82979'})
frozenset({'55327', '55375', '55295', '55323', '222375'})
frozenset({'80203', '81843', '222787', '81939', '89829', '81875', '89845', '222783', '222795', '86979', '222455', '89849', '81943', '222771', '81931', '80027'})
frozenset({'84827', '78163', '84803'})
frozenset({'222591'})
frozenset({'56181', '89453', '55287', '55283'})
frozenset({'81959', '81955', '81975'})
frozenset({'55595'})
frozenset({'84795', '228995', '84731'})
frozenset({'55779'})
frozenset({'228795'})
frozen

frozenset({'55271', '55267', '55319'})
frozenset({'56717'})
frozenset({'84755', '84735'})
frozenset({'56037', '222643'})
frozenset({'55491'})
frozenset({'89745'})
frozenset({'56297', '55927', '56277', '56273', '55543', '55651', '222899', '222883', '56225', '55783', '222471'})
frozenset({'83263', '83179', '83167'})
frozenset({'203733'})
frozenset({'55883', '55879', '222607', '55855', '222615', '222611'})
frozenset({'81647'})
frozenset({'228991', '81603', '83235', '86043', '203733', '203729', '84815'})
frozenset({'87275'})
frozenset({'84735'})
frozenset({'83947', '86459', '86999', '81975'})
frozenset({'78691'})
frozenset({'56401', '222499', '55811', '222495', '222963', '56561', '56549', '55783', '222491'})
frozenset({'85315'})
frozenset({'81851', '81835', '86143', '89653', '86203', '84243', '84199', '81863'})
frozenset({'55491', '222535', '55483', '222591', '55463', '55803', '55487', '55559'})
frozenset({'56393', '56353', '223019', '223051', '56397', '56405', '56225', '223023', '222919'}

frozenset({'89721', '86499', '55463', '222383', '55475'})
frozenset({'55491', '222379', '56561', '55651', '55487'})
frozenset({'222663'})
frozenset({'55323', '55267'})
frozenset({'81615'})
frozenset({'56037', '81587', '203729', '56041'})
frozenset({'84207'})
frozenset({'83999', '83983', '83963', '82875', '83971', '83979'})
frozenset({'83943', '83939'})
frozenset({'86055', '203733', '203729'})
frozenset({'86263', '86775'})
frozenset({'55351', '55883', '55835', '55515', '89745', '55831', '56057'})
frozenset({'83851', '89441', '83891', '83923', '83183'})
frozenset({'55351', '55275', '55283'})
frozenset({'55491', '222379', '222383', '55479', '55475', '55487'})
frozenset({'222951'})
frozenset({'89349', '83411', '83551', '89329', '83403', '89345', '83159', '83183', '83275', '89357', '83147', '89353', '83611', '83567'})
frozenset({'88579', '88531', '89453', '88535'})
frozenset({'83851'})
frozenset({'222403', '55411', '222343'})
frozenset({'81699', '89757', '89829', '89433', '86895', '81707', 

frozenset({'55875', '55879', '55859', '55843'})
frozenset({'55815', '56065'})
frozenset({'86483', '78599', '198453'})
frozenset({'55887'})
frozenset({'55807', '55803'})
frozenset({'89681'})
frozenset({'55267', '244115', '55315', '55319', '55295'})
frozenset({'56769', '244179', '55527', '55539'})
frozenset({'55451'})
frozenset({'55343'})
frozenset({'82819', '82811'})
frozenset({'86403', '86735', '86415'})
frozenset({'228823'})
frozenset({'82027', '80195'})
frozenset({'229127', '86591', '81639'})
frozenset({'86043'})
frozenset({'55283'})
frozenset({'244259'})
frozenset({'55555', '83523', '83511', '83227', '83527', '55287', '83515'})
frozenset({'82859', '83159'})
frozenset({'84047', '84079', '83395'})
frozenset({'85887', '87319', '79539', '87323'})
frozenset({'55271', '222559', '244303', '244199', '244311', '244347', '244223'})
frozenset({'244199', '56037', '55543', '55619', '55531'})
frozenset({'80051', '83687', '86407', '82587', '83703', '83471', '81843', '86475', '83487', '87135', '894

frozenset({'55535', '55271', '222971', '56765'})
frozenset({'56281', '244135'})
frozenset({'87039'})
frozenset({'88751'})
frozenset({'244107', '55271'})
frozenset({'80291', '85883', '78191', '85887', '85855', '85799', '229043', '85879'})
frozenset({'84051'})
frozenset({'78995', '79011', '79019', '85119'})
frozenset({'244411', '56065', '244423', '222691'})
frozenset({'222439', '55283'})
frozenset({'88623'})
frozenset({'85619', '78715', '78719', '78687'})
frozenset({'222975', '55779', '55367', '56061', '56353', '56761', '244279', '55455', '56049', '56765', '222575', '56769', '222971', '55435', '56349', '244327', '222363', '244291'})
frozenset({'55643'})
frozenset({'56057', '244531', '222835', '56561'})
frozenset({'86947'})
frozenset({'55271', '55367', '55379', '55283', '244107', '55403'})
frozenset({'89629'})
frozenset({'82795', '82807'})
frozenset({'86919', '86907', '86923', '86911', '86943', '86931', '86927'})
frozenset({'87043', '87035', '87027', '87111', '87075', '87031', '87019', '8

...

frozenset({'55363'})
frozenset({'81615', '203741', '305497', '272155', '271847'})
frozenset({'56037', '304533', '222643'})
frozenset({'55323'})
frozenset({'305441', '305405', '55443', '55363', '55359', '55451', '253633', '314769', '55287', '55447'})
frozenset({'305521'})
frozenset({'55803'})
frozenset({'85003'})
frozenset({'78587'})
frozenset({'56241'})
frozenset({'244251', '305537'})
frozenset({'84755', '305849', '56165', '314885', '250331', '56549', '290543', '84839', '250427', '289133', '56161', '84767', '305853', '84743'})
frozenset({'81631', '272039'})
frozenset({'56061'})
frozenset({'89813', '55335', '55323', '271847', '88563'})
frozenset({'55323'})
frozenset({'291033', '314857', '314853', '56149', '56125', '56141', '88969'})
frozenset({'305497', '55755', '55539'})
frozenset({'56037'})
frozenset({'88953', '88683', '288441', '82879'})
frozenset({'83723', '86143', '86079', '86839', '81591'})
frozenset({'305401', '55283', '253633', '55323', '55275', '55319', '55295', '55335'})
froze

frozenset({'305753', '55999', '55995', '305741', '56015', '55935'})
frozenset({'82719'})
frozenset({'56281'})
frozenset({'55267', '86195', '83479', '86203', '88427', '271663'})
frozenset({'82359', '88071', '88043', '88067', '89701', '83879'})
frozenset({'56569', '306069', '56577'})
frozenset({'81627'})
frozenset({'84835', '84811', '84759', '84743'})
frozenset({'272155', '89713', '89725'})
frozenset({'55543', '55555', '55559'})
frozenset({'55779', '316993', '56165', '250331', '290543', '55655', '56169', '55531'})
frozenset({'55927', '55943', '56003', '222627'})
frozenset({'56609'})
frozenset({'250363', '55755', '250327'})
frozenset({'327147', '327115', '327127', '271847'})
frozenset({'81615', '84783', '55327', '82719', '84779'})
frozenset({'55755', '250455', '55779', '56557'})
frozenset({'55551', '56065', '55267', '56273', '55619'})
frozenset({'88953', '288441', '81627'})
frozenset({'88775', '88779'})
frozenset({'81179', '81187', '81199', '81203'})
frozenset({'55599', '55603', '305477'}

frozenset({'55675', '55703'})
frozenset({'87279', '87275', '87283'})
frozenset({'305417', '79263', '305409'})
frozenset({'326063', '326067'})
frozenset({'55867', '55851'})
frozenset({'81203'})
frozenset({'229015', '327509', '84663', '84643', '89433', '84659', '84995', '83015', '84639', '83047'})
frozenset({'306145', '250411'})
frozenset({'82719', '89953', '83379'})
frozenset({'86187', '78619', '80127', '83255', '78247', '79259', '87275', '289029', '78611', '79523', '79315', '86243'})
frozenset({'89949', '88827', '87363', '79259', '79315'})
frozenset({'86835', '86783', '86691'})
frozenset({'55547', '55563', '55551', '55555', '55543', '55411', '55407', '222399', '244135', '55559'})
frozenset({'78875'})
frozenset({'84843', '81179'})
frozenset({'89729', '326131', '89717', '79039', '80427', '79795', '89745', '88427', '89701', '89877'})
frozenset({'89721', '228971', '271683', '78191', '78791', '81515', '86735', '83673', '86403', '83171', '85903', '271727', '85899', '83263', '326123'})
frozen

frozenset({'85659', '229175', '88539', '89765', '271847', '85467'})
frozenset({'305529', '305405'})
frozenset({'314917', '86175', '86071', '305929'})
frozenset({'55291', '305405', '55323', '85911', '89453', '55319', '84843', '271839', '248129'})
frozenset({'86919', '82771', '89813', '81639', '89761', '83415', '83583', '83255', '86071', '89837', '89797', '81567'})
frozenset({'326127', '326115'})
frozenset({'272023', '272015', '272031', '272019', '203733', '203729'})
frozenset({'229179', '82671'})
frozenset({'244251', '81583', '244315'})
frozenset({'327155', '306129'})
frozenset({'326103'})
frozenset({'81647', '322509'})
frozenset({'305405', '55327', '250267', '55323', '55307'})
frozenset({'83263', '228967', '82663', '272111'})
frozenset({'306041', '305453'})
frozenset({'305865', '55627'})
frozenset({'81243', '81287', '85235', '85887', '86347', '86367', '81267', '81311', '82607', '85919', '86691'})
frozenset({'305937', '250351', '83723', '82523', '56293'})
frozenset({'250267', '55551'})


frozenset({'55367', '55267', '55387'})
frozenset({'83339', '83579'})
frozenset({'55655'})
frozenset({'305497', '239699', '305577', '305581'})
frozenset({'244203'})
frozenset({'290543', '56037', '222643', '56161', '304533', '56023'})
frozenset({'56769', '56761'})
frozenset({'55655'})
frozenset({'55351', '55271', '55267', '290543', '55387'})
frozenset({'314893', '250523'})
frozenset({'79287', '83995', '84735'})
frozenset({'83743'})
frozenset({'305865', '56629', '56601', '250539', '56609', '55719'})
frozenset({'85911', '85903'})
frozenset({'250267'})
frozenset({'56769'})
frozenset({'203733'})
frozenset({'56593', '306173', '84731'})
frozenset({'55547', '55555', '55543', '55535', '55531', '55559'})
frozenset({'79263', '79807', '79815', '79651', '79239'})
frozenset({'314769', '55271', '55439', '55355'})
frozenset({'228727', '78215', '327519', '82631', '78031', '78939', '78907', '78187', '78903'})
frozenset({'85199'})
frozenset({'86047', '55267', '55283', '55455', '235917', '326095', '88969'}

In [94]:
itemSet, transactionList = getItemSetTransactionList(data)

In [103]:
itemSet

{frozenset({'253673'}),
 frozenset({'306213'}),
 frozenset({'87187'}),
 frozenset({'81067'}),
 frozenset({'55655'}),
 frozenset({'89557'}),
 frozenset({'82811'}),
 frozenset({'84091'}),
 frozenset({'285433'}),
 frozenset({'84055'}),
 frozenset({'250535'}),
 frozenset({'82963'}),
 frozenset({'78051'}),
 frozenset({'79859'}),
 frozenset({'85007'}),
 frozenset({'81283'}),
 frozenset({'88671'}),
 frozenset({'79351'}),
 frozenset({'78795'}),
 frozenset({'86087'}),
 frozenset({'305517'}),
 frozenset({'306373'}),
 frozenset({'84267'}),
 frozenset({'81971'}),
 frozenset({'84111'}),
 frozenset({'86963'}),
 frozenset({'86619'}),
 frozenset({'250395'}),
 frozenset({'239711'}),
 frozenset({'222975'}),
 frozenset({'55419'}),
 frozenset({'85619'}),
 frozenset({'82691'}),
 frozenset({'90021'}),
 frozenset({'253637'}),
 frozenset({'84763'}),
 frozenset({'86647'}),
 frozenset({'55471'}),
 frozenset({'222351'}),
 frozenset({'198449'}),
 frozenset({'89725'}),
 frozenset({'321317'}),
 frozenset({'84923'})

In [104]:
freqSet = defaultdict(int)
oneCSet = returnItemsWithMinSupport(itemSet, transactionList, 0.2, freqSet)

In [17]:
(transactions)

[]